## Stream / Face Expression

This notebook uses the streaming API to analyze a stream of face images.

In [9]:
import asyncio
import traceback

from utilities import download_file, print_emotions

from hume import HumeStreamClient
from hume.models.config import FaceConfig
import cv2
import base64
from pathlib import Path
from PIL import Image
import io

In [33]:
def encode_data(filepath: Path) -> str:
    with Path(filepath).open('rb') as fp:
        bytes_data = base64.b64encode(fp.read())
        encoded_data = bytes_data.decode("utf-8")
        return encoded_data

In [32]:
filepath = "data/Test_Image_Hume.png"

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")
        
        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        async with client.connect([config]) as socket:
            result = await socket.send_file(filepath)
            emotions = result["face"]["predictions"][0]["emotions"]
            print_emotions(emotions)
    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook you do not need these lines.
# Jupyter has its own async event loop, so this merges main into the Jupyter event loop.
# To run this sample in a script with asyncio you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())

<Task pending name='Task-5843' coro=<main() running at C:\Users\phili\AppData\Local\Temp\ipykernel_18712\3950561621.py:3>>

- Joy: 0.305439
- Sadness: 0.095025
- Anger: 0.042541


## Example Extracting Frames from a video

In [18]:
cap = cv2.VideoCapture("data/Test_Ausschnitt_Hume.mp4")  # Or use cv2.VideoCapture(0) for camera

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    cv2.imshow('Frame', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()


In [31]:
cap = cv2.VideoCapture("data/Test_Ausschnitt_Hume.mp4") 

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")
        
        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        async with client.connect([config]) as socket:

            while cap.isOpened():
                ret, frame = cap.read()
                if not ret:
                    break

                # Convert the OpenCV frame to PIL image format
                frame_pil = Image.fromarray(cv2.cvtColor(frame, cv2.COLOR_BGR2RGB))

                # Create a BytesIO object to store the image data
                image_stream = io.BytesIO()

                # Save the PIL image as PNG to the BytesIO object
                frame_pil.save(image_stream, format='PNG')

                # Get the encoded image data as bytes
                image_bytes = image_stream.getvalue()

                # Encode the image bytes as base64
                encoded_image = base64.b64encode(image_bytes)

                # # Pass the encoded image as a file-like object
                # file_object = io.BytesIO(encoded_image.encode('utf-8'))

                # Display the frame
                #cv2.imshow('Frame', frame)
                result = await socket.send_bytes(encoded_image)
                emotions = result["face"]["predictions"][0]["emotions"]
                print_emotions(emotions)

                if cv2.waitKey(1) & 0xFF == ord('q'):
                    break

            cap.release()
            cv2.destroyAllWindows()

           
    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook you do not need these lines.
# Jupyter has its own async event loop, so this merges main into the Jupyter event loop.
# To run this sample in a script with asyncio you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())

<Task pending name='Task-5837' coro=<main() running at C:\Users\phili\AppData\Local\Temp\ipykernel_18712\3036162858.py:3>>

Traceback (most recent call last):
  File "C:\Users\phili\AppData\Local\Temp\ipykernel_18712\3036162858.py", line 37, in main
    emotions = result["face"]["predictions"][0]["emotions"]
KeyError: 'predictions'



In [20]:
cap = cv2.VideoCapture('data/Test_Ausschnitt_Hume.mp4')  # Or use cv2.VideoCapture(0) for camera

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Convert the OpenCV frame to PIL image format
    frame_pil = Image.fromarray(cv2.cvtColor(frame, cv2.COLOR_BGR2RGB))

    # Create a BytesIO object to store the image data
    image_stream = io.BytesIO()

    # Save the PIL image as PNG to the BytesIO object
    frame_pil.save(image_stream, format='PNG')

    # Get the encoded image data as bytes
    image_bytes = image_stream.getvalue()

    # Encode the image bytes as base64
    encoded_image = base64.b64encode(image_bytes).decode('utf-8')

    # Display the frame
    cv2.imshow('Frame', frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()


...


https://docs.hume.ai/doc/streaming-api/operation/operation-publish-language

The documentation suggests to stream videofile data as the following: "Note: Streaming video files is not recommended. For better latency you should stream videos by sending a single frame image in each payload."

In [ ]:
filepath = "data/obama.png"

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")
        
        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        async with client.connect([config]) as socket:
            result = await socket.send_file(filepath)
            emotions = result["face"]["predictions"][0]["emotions"]
            print_emotions(emotions)
    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook you do not need these lines.
# Jupyter has its own async event loop, so this merges main into the Jupyter event loop.
# To run this sample in a script with asyncio you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())

In [ ]:
filepath = "data/COIN Edit_Test1.mp4"

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")
        
        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        
        async with client.connect([config]) as socket:
            async def capture_video_frames():
                video_capture = cv2.VideoCapture(filepath)

                while True:
                    ret, frame = video_capture.read()

                    if not ret:
                        break

                    frame_data = frame.tobytes()
                    yield frame_data

                video_capture.release()
            video_frames = capture_video_frames()




            video_frames = [frame async for frame in capture_video_frames()]
            result = await socket.send_file(video_frames)
            emotions = result["face"]["predictions"][0]["emotions"]
            print_emotions(emotions)
            await asyncio.sleep(0.01)

    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook you do not need these lines.
# Jupyter has its own async event loop, so this merges main into the Jupyter event loop.
# To run this sample in a script with asyncio you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())

In [ ]:
import traceback


filepath = "data/COIN Edit_Test1.mp4"

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")

        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        async with client.connect([config]) as socket:
            async def capture_video_frames():
                video_capture = cv2.VideoCapture(filepath)

                while True:
                    ret, frame = video_capture.read()

                    if not ret:
                        break

                    frame_data = frame.tobytes()
                    yield frame_data

                video_capture.release()

            video_frames = capture_video_frames()

            await socket.send_file(video_frames)

            # Retrieve and print emotions
            async for result in socket.receive_results():
                emotions = result["face"]["predictions"][0]["emotions"]
                print_emotions(emotions)
                await asyncio.sleep(0.01)

    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook, you do not need these lines.
# Jupyter has its own async event loop, so this merges `main` into the Jupyter event loop.
# To run this sample in a script with asyncio, you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())


In [ ]:
filepath = "data/COIN Edit_Test1.mp4"

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")

        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        async with client.connect([config]) as socket:
            def capture_video_frames():
                video_capture = cv2.VideoCapture(filepath)

                while True:
                    ret, frame = video_capture.read()

                    if not ret:
                        break

                    frame_data = frame.tobytes()
                    yield frame_data

                video_capture.release()

            video_frames = capture_video_frames()

            await socket.send_file(video_frames)

            # Retrieve and print emotions
            async for result in socket.receive_results():
                emotions = result["face"]["predictions"][0]["emotions"]
                print_emotions(emotions)
                await asyncio.sleep(0.01)

    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook, you do not need these lines.
# Jupyter has its own async event loop, so this merges `main` into the Jupyter event loop.
# To run this sample in a script with asyncio, you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())


In [ ]:
video_data = "data/COIN Edit_Test1.mp4"

def encode_data(filepath: Path) -> str:
    with Path(filepath).open('rb') as fp:
        bytes_data = base64.b64encode(fp.read())
        encoded_data = bytes_data.decode("utf-8")
        return encoded_data

encoded_data = encode_data(video_data)
print(encoded_data)

async def main():
    try:
        client = HumeStreamClient("8vNtx0WMeAGVbdx7fiFOyhmYnnDq6BAP3B288un270N60oJa")

        # Enable face identification to track unique faces over the streaming session
        config = FaceConfig(identify_faces=True)
        async with client.connect([config]) as socket:
            async def capture_video_frames():
                video_capture = cv2.VideoCapture(video_data)

                while True:
                    ret, frame = video_capture.read()

                    if not ret:
                        break

                    frame_data = frame.tobytes()
                    yield frame_data

                video_capture.release()

            video_frames = capture_video_frames()

            async for frame in video_frames:
                await socket.send_file(frame)
                await asyncio.sleep(0.01)  # Adjust sleep time as needed

            # Retrieve and print emotions
            async for result in socket.receive_results():
                emotions = result["face"]["predictions"][0]["emotions"]
                print_emotions(emotions)
                await asyncio.sleep(0.01)

    except Exception:
        print(traceback.format_exc())

# When running the streaming API outside of a Jupyter notebook, you do not need these lines.
# Jupyter has its own async event loop, so this merges `main` into the Jupyter event loop.
# To run this sample in a script with asyncio, you can use `asyncio.run(main())`
loop = asyncio.get_event_loop()
loop.create_task(main())
